# TITLE:
## Analysis  of Neighbourhoods in Perth, Western Australia, for business, contractors and job seekers to be able make better decisions on where to work and where to start a business.

# INTRODUCTION [Western Australia](https://en.wikipedia.org/wiki/Western_Australia)
### Western Australia has the highest GDP/GSP per capita of any state in Australia, for 2019/2020 this was ~110000 AUD. This GDP/GSP value also makes the global top ten GDP list if Western Australia where a seperate country. Western Australia's political stability, attractive Mediterranean type climate of hot summers and mild wet winters and a labour shortage makes the Capital City Perth a desirable location to move too in search of opportunity. Perth's isolation and low population density has also helped control the spread of COVID-19. Apart from the ocassional short lockdown, lifestyle is more or less back to the normal pre 2020 level.

### [Perth](https://en.wikipedia.org/wiki/Perth) has one of the lowest population densities of any of the major cities in the World and is spread out along the Indian Ocean Coast from Dawesville to Yanchep, a distance of 121 Km ([Haversine](https://en.wikipedia.org/wiki/Haversine_formula)). The road transportation network is now well developed and personal automobiles is the prefered mode of transport. There are suburban rail and bus networks. The rail network is mainly used for workers commuting to the CBD. There are continuing developments in these areas including a rail link to Perth International airport.

### The rapid growth of Perth and Western Australia since the discovery of iron ore in the Pilbra in the 1950s has resulted in considerable opportunity not only in the mining industry but throughout the state. Western Australia is also a significant gold and agricultural producer and is one of the great grain growing areas of the World. The hazards and the remote locations of most of the mines has produced a "fly in fly out" FIFO culture which is very well paid. I have personally heard people who have worked and are working in the mining industry boasting of pay off their family home morgages in 3 years? The rapid growth of the surburbs have resulted in the shortage of amneties and hence opportunities for business. For, example when I was living in Aveley in 2011 I could only find one petrol station in the entire Ellenbrook/Aveley/TheVines area; these suburbs have a combined  population of over 60000.

### The methodology to provide information that businesses, contactors, and employees can use to make decisions uses a combination of suburb geolocation data, venue information using the foursquare API, a machine learning algorithm K-means clustering for clustering similar suburbs with similar venues and attributes, and median house price data for randomly selected suburbs. A multiple linear regression analysis will attempt to build a model to predict house median house price (dependant variable) in suburbs using two independant varibales, distance from CBD, and distance from the coast. The geolocation data will be used to calculate the distances using the Haversine calculation. This will explained in more detail in the next section.



In [2]:
pip install geopy

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install folium

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
     |████████████████████████████████| 94 kB 6.9 MB/s  eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [4]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


### Covert  Western_Australia_Post_Geo.csv file to pandas dataframe
[Loading and accessing data in a Notebook Watson Studio](https://www.ibm.com/support/producthub/icpdata/docs/content/SSQNUZ_latest/wsj/analyze-data/load-and-access-data.html)

The above file was edited in Excel from another file Australia_Post..._Geolocation.csv
to provide only postcodes in the Perth Metro Area

In [9]:

import os, types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.

if os.environ.get('RUNTIME_ENV_LOCATION_TYPE') == 'external':
    endpoint_23e3b5aeac9043948fc832b12320c85a = 'https://s3.us.cloud-object-storage.appdomain.cloud'
else:
    endpoint_23e3b5aeac9043948fc832b12320c85a = 'https://s3.private.us.cloud-object-storage.appdomain.cloud'

client_23e3b5aeac9043948fc832b12320c85a = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='_XPN9PaWgIin6_24Ab5q8W8raEbafWxrcOduTygF64P8',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url=endpoint_23e3b5aeac9043948fc832b12320c85a)

body = client_23e3b5aeac9043948fc832b12320c85a.get_object(Bucket='ibmdscapstoneweel3toronto-donotdelete-pr-uew1iz4itwgorw',Key='Western_Australia_Post_Geo.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_3 = pd.read_csv(body)
df_data_3.head()


postcode           suburb state            dc  \
0      6161  ROTTNEST ISLAND    WA    PALMYRA DC   
1      6035          YANCHEP    WA  JOONDALUP DC   
2      6211       DAWESVILLE    WA   MANDURAH DC   
3      6210         WANNANUP    WA   MANDURAH DC   
4      6210           FALCON    WA   MANDURAH DC   

                                            type        lat         lon  
0  Delivery Area                                 -32.007488  115.503938  
1  Delivery Area                                 -31.546670  115.632045  
2  Delivery Area                                 -32.634691  115.634411  
3  Delivery Area                                 -32.598055  115.643883  
4  Delivery Area                                 -32.589738  115.647291

In [15]:
df_data_3.shape

(382, 7)

#### Perth postcodes between Dawsville and Yancep Latitudes -32.634691 and -31.546670
#### and longitudes Mundaring 116.168204 and Rottnest Island 115.503938

#### and longitudes Mundaring 116.168205 and Rottnest Island 115.503938

In [9]:
df_Perth_WAA = df_data_3.rename(columns = {'suburb':'Neighborhood'})

df_Perth_WAA

postcode            Neighborhood state                    dc  \
0        6161         ROTTNEST ISLAND    WA            PALMYRA DC   
1        6035                 YANCHEP    WA          JOONDALUP DC   
2        6211              DAWESVILLE    WA           MANDURAH DC   
3        6210                WANNANUP    WA           MANDURAH DC   
4        6210                  FALCON    WA           MANDURAH DC   
5        6210              HALLS HEAD    WA           MANDURAH DC   
6        6036                JINDALEE    WA          JOONDALUP DC   
7        6168           GARDEN ISLAND    WA         ROCKINGHAM DC   
8        6168                   PERON    WA         ROCKINGHAM DC   
9        6030                MINDARIE    WA          JOONDALUP DC   
10       6210                 ERSKINE    WA           MANDURAH DC   
11       6030            QUINNS ROCKS    WA          JOONDALUP DC   
12       6036                  BUTLER    WA          JOONDALUP DC   
13       6169              SHOALWATER    WA         ROCKINGHAM DC   
14       6169              SAFETY BAY    WA         ROCKINGHAM DC   
15       6030                 MERRIWA    WA          JOONDALUP DC   
16       6028             BURNS BEACH    WA          JOONDALUP DC   
17       6030               RIDGEWOOD    WA          JOONDALUP DC   
18       6030                CLARKSON    WA          JOONDALUP DC   
19       6030             TAMALA PARK    WA          JOONDALUP DC   
20       6038                 ALKIMOS    WA          JOONDALUP DC   
21       6210             DUDLEY PARK    WA           MANDURAH DC   
22       6028                   ILUKA    WA          JOONDALUP DC   
23       6168        ROCKINGHAM BEACH    WA         ROCKINGHAM DC   
24       6210                MANDURAH    WA           MANDURAH DC   
25       6210            SILVER SANDS    WA           MANDURAH DC   
26       6027              OCEAN REEF    WA          JOONDALUP DC   
27       6028                 KINROSS    WA          JOONDALUP DC   
28       6032                NOWERGUP    WA          JOONDALUP DC   
29       6210          MANDURAH NORTH    WA           MANDURAH DC   
30       6210           MANDURAH EAST    WA           MANDURAH DC   
31       6025                HILLARYS    WA          JOONDALUP DC   
32       6027                MULLALOO    WA          JOONDALUP DC   
33       6210                SAN REMO    WA           MANDURAH DC   
34       6028              CURRAMBINE    WA          JOONDALUP DC   
35       6025                KALLAROO    WA          JOONDALUP DC   
36       6168              ROCKINGHAM    WA         ROCKINGHAM DC   
37       6033               CARABOODA    WA          JOONDALUP DC   
38       6027                CONNOLLY    WA          JOONDALUP DC   
39       6020                SORRENTO    WA             GWELUP DC   
40       6173          SECRET HARBOUR    WA           MANDURAH DC   
41       6174              GOLDEN BAY    WA           MANDURAH DC   
42       6168         EAST ROCKINGHAM    WA         ROCKINGHAM DC   
43       6210          MEADOW SPRINGS    WA           MANDURAH DC   
44       6020                 MARMION    WA             GWELUP DC   
45       6210              MADORA BAY    WA           MANDURAH DC   
46       6210                COODANUP    WA           MANDURAH DC   
47       6159         NORTH FREMANTLE    WA            PALMYRA DC   
48       6020             NORTH BEACH    WA             GWELUP DC   
49       6029                   TRIGG    WA             GWELUP DC   
50       6172            PORT KENNEDY    WA         ROCKINGHAM DC   
51       6015              CITY BEACH    WA             GWELUP DC   
52       6169                 WAIKIKI    WA         ROCKINGHAM DC   
53       6169                 WARNBRO    WA         ROCKINGHAM DC   
54       6027                  BELDON    WA          JOONDALUP DC   
55       6175               SINGLETON    WA           MANDURAH DC   
56       6012             MOSMAN PARK    WA           NEDLANDS DC   
57 

In [10]:
df_Perth_WAA.shape

(382, 7)

#### There is what appears to be duplicates for ther Perth City distrubtion centre but they all have different postcodes

In [11]:
df_Perth_West = df_Perth_WAA.drop(columns=['state','type'])
df_Perth_West

postcode            Neighborhood                    dc        lat  \
0        6161         ROTTNEST ISLAND            PALMYRA DC -32.007488   
1        6035                 YANCHEP          JOONDALUP DC -31.546670   
2        6211              DAWESVILLE           MANDURAH DC -32.634691   
3        6210                WANNANUP           MANDURAH DC -32.598055   
4        6210                  FALCON           MANDURAH DC -32.589738   
5        6210              HALLS HEAD           MANDURAH DC -32.549355   
6        6036                JINDALEE          JOONDALUP DC -31.644341   
7        6168           GARDEN ISLAND         ROCKINGHAM DC -32.225759   
8        6168                   PERON         ROCKINGHAM DC -32.278879   
9        6030                MINDARIE          JOONDALUP DC -31.685654   
10       6210                 ERSKINE           MANDURAH DC -32.557169   
11       6030            QUINNS ROCKS          JOONDALUP DC -31.672941   
12       6036                  BUTLER          JOONDALUP DC -31.649385   
13       6169              SHOALWATER         ROCKINGHAM DC -32.295540   
14       6169              SAFETY BAY         ROCKINGHAM DC -32.303433   
15       6030                 MERRIWA          JOONDALUP DC -31.666754   
16       6028             BURNS BEACH          JOONDALUP DC -31.729200   
17       6030               RIDGEWOOD          JOONDALUP DC -31.663830   
18       6030                CLARKSON          JOONDALUP DC -31.677452   
19       6030             TAMALA PARK          JOONDALUP DC -31.707482   
20       6038                 ALKIMOS          JOONDALUP DC -32.289149   
21       6210             DUDLEY PARK           MANDURAH DC -32.540594   
22       6028                   ILUKA          JOONDALUP DC -31.737276   
23       6168        ROCKINGHAM BEACH         ROCKINGHAM DC -32.273782   
24       6210                MANDURAH           MANDURAH DC -32.533010   
25       6210            SILVER SANDS           MANDURAH DC -32.510602   
26       6027              OCEAN REEF          JOONDALUP DC -31.752177   
27       6028                 KINROSS          JOONDALUP DC -31.718375   
28       6032                NOWERGUP          JOONDALUP DC -31.642666   
29       6210          MANDURAH NORTH           MANDURAH DC -32.515318   
30       6210           MANDURAH EAST           MANDURAH DC -32.515318   
31       6025                HILLARYS          JOONDALUP DC -31.809421   
32       6027                MULLALOO          JOONDALUP DC -31.778989   
33       6210                SAN REMO           MANDURAH DC -32.488900   
34       6028              CURRAMBINE          JOONDALUP DC -31.735025   
35       6025                KALLAROO          JOONDALUP DC -31.790785   
36       6168              ROCKINGHAM         ROCKINGHAM DC -32.288048   
37       6033               CARABOODA          JOONDALUP DC -31.603480   
38       6027                CONNOLLY          JOONDALUP DC -31.754230   
39       6020                SORRENTO             GWELUP DC -31.825368   
40       6173          SECRET HARBOUR           MANDURAH DC -32.402574   
41       6174              GOLDEN BAY           MANDURAH DC -32.429853   
42       6168         EAST ROCKINGHAM         ROCKINGHAM DC -32.258299   
43       6210          MEADOW SPRINGS           MANDURAH DC -32.494802   
44       6020                 MARMION             GWELUP DC -31.844038   
45       6210              MADORA BAY           MANDURAH DC -32.465347   
46       6210                COODANUP           MANDURAH DC -32.550988   
47       6159         NORTH FREMANTLE            PALMYRA DC -32.029041   
48       6020             NORTH BEACH             GWELUP DC -31.860972   
49       6029                   TRIGG             GWELUP DC -31.876031   
50       6172            PORT KENNEDY         ROCKINGHAM DC -32.375470   
51       6015              CITY BEACH             GWELUP DC -31.938276   
52       6169                 WAIKIKI         ROCKINGHAM DC -32.314919   
53       

## Geographicalcoordinates of Perth City WA  are

In [12]:
address = 'Perth City, WA'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Perth City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Perth City are -31.9527121, 115.8604796.


In [13]:
# create map of Toronto using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, dc, suburb in zip(df_Perth_West['lat'], df_Perth_West['lon'], df_Perth_West['dc'], df_Perth_West['Neighborhood']):
    label = '{}, {}'.format(suburb, dc)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Foursquare Credentials

In [14]:
CLIENT_ID = '4ECWPTCW4UGYZURT4HN22B5NTHU2GRMI5HARQVLDCRBEOX42' # your Foursquare ID
CLIENT_SECRET = 'W0R3HIC4JEFJMNIHJCGPFC3NSPTUVSD43RCOKI0LIPQOEZYC' # your Foursquare Secret
ACCESS_TOKEN = 'RWRCU4ONBF4N1EVNFCMWTOPL2F0Q5FIQ4PTGEUQTMEPUMVV3' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 4ECWPTCW4UGYZURT4HN22B5NTHU2GRMI5HARQVLDCRBEOX42
CLIENT_SECRET:W0R3HIC4JEFJMNIHJCGPFC3NSPTUVSD43RCOKI0LIPQOEZYC


### PERTH ST GEORGES TCE	WA	CITY DELIVERY CENTRE	Post Office Boxes	-31.955050	115.857527

In [57]:
df_Perth_West.loc[240, 'dc']

'CITY DELIVERY CENTRE'

In [15]:
neighborhood_latitude = df_Perth_West.loc[256, 'lat'] # neighborhood latitude value
neighborhood_longitude = df_Perth_West.loc[256, 'lon'] # neighborhood longitude value

neighborhood_name = df_Perth_West.loc[256, 'dc'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of CITY DELIVERY CENTRE are -31.924073999999997, 115.91223000000001.


In [16]:

LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius


url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL



'https://api.foursquare.com/v2/venues/explore?&client_id=4ECWPTCW4UGYZURT4HN22B5NTHU2GRMI5HARQVLDCRBEOX42&client_secret=W0R3HIC4JEFJMNIHJCGPFC3NSPTUVSD43RCOKI0LIPQOEZYC&v=20180604&ll=-31.924073999999997,115.91223000000001&radius=500&limit=100'

In [17]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '60ddb662e008bd7847cf4836'},
 'response': {'headerLocation': 'Bayswater',
  'headerFullLocation': 'Bayswater, Perth',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 4,
  'suggestedBounds': {'ne': {'lat': -31.91957399549999,
    'lng': 115.91752202321942},
   'sw': {'lat': -31.928574004500003, 'lng': 115.9069379767806}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bed3d653372c928874d1114',
       'name': 'Liquor Barons Bayswater',
       'location': {'lat': -31.925394064844504,
        'lng': 115.91042193398533,
        'labeledLatLngs': [{'label': 'display',
          'lat': -31.925394064844504,
          'lng': 115.91042193398533}],
        'distance': 225,
        'cc': 'AU',
        'country': 'Australia',
   

In [18]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [19]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/ipykernel/__main__.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  app.launch_new_instance()


name           categories        lat  \
0                Liquor Barons Bayswater         Liquor Store -31.925394   
1                     Corleone Pizza Bar          Pizza Place -31.925926   
2                   Bayswater Car Rental  Rental Car Location -31.925850   
3  Bayswater Bowling and Recreation Club          Sports Club -31.922721   

          lng  
0  115.910422  
1  115.910445  
2  115.908980  
3  115.907223

In [20]:
nearby_venues.head(30)

name           categories        lat  \
0                Liquor Barons Bayswater         Liquor Store -31.925394   
1                     Corleone Pizza Bar          Pizza Place -31.925926   
2                   Bayswater Car Rental  Rental Car Location -31.925850   
3  Bayswater Bowling and Recreation Club          Sports Club -31.922721   

          lng  
0  115.910422  
1  115.910445  
2  115.908980  
3  115.907223

## Perth Metro Venues

In [21]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [22]:
PerthMetro_venues = getNearbyVenues(names=df_Perth_West['Neighborhood'],
                                   latitudes=df_Perth_West['lat'],
                                   longitudes=df_Perth_West['lon']
                                  )

ROTTNEST ISLAND
YANCHEP
DAWESVILLE
WANNANUP
FALCON
HALLS HEAD
JINDALEE
GARDEN ISLAND
PERON
MINDARIE
ERSKINE
QUINNS ROCKS
BUTLER
SHOALWATER
SAFETY BAY
MERRIWA
BURNS BEACH
RIDGEWOOD
CLARKSON
TAMALA PARK
ALKIMOS
DUDLEY PARK
ILUKA
ROCKINGHAM BEACH
MANDURAH
SILVER SANDS
OCEAN REEF
KINROSS
NOWERGUP
MANDURAH NORTH
MANDURAH EAST
HILLARYS
MULLALOO
SAN REMO
CURRAMBINE
KALLAROO
ROCKINGHAM
CARABOODA
CONNOLLY
SORRENTO
SECRET HARBOUR
GOLDEN BAY
EAST ROCKINGHAM
MEADOW SPRINGS
MARMION
MADORA BAY
COODANUP
NORTH FREMANTLE
NORTH BEACH
TRIGG
PORT KENNEDY
CITY BEACH
WAIKIKI
WARNBRO
BELDON
SINGLETON
MOSMAN PARK
SOUTH FREMANTLE
EAST FREMANTLE
GREENFIELDS
SCARBOROUGH
NORTH PERTH
CLAREMONT NORTH
COOLOONGUP
COTTESLOE
HEATHRIDGE
BEACONSFIELD
FREMANTLE
COOGEE
DUNCRAIG
PEPPERMINT GROVE
WHITE GUM VALLEY
PADBURY
CRAIGIE
JOONDALUP
HILLMAN
HENDERSON
SWANBOURNE
FURNISSDALE
NEERABUP
WEMBLEY DOWNS
PALMYRA
KWINANA BEACH
CARRAMAR
CARINE
MOUNT CLAREMONT
DOUBLEVIEW
NIRIMBA
HAMILTON HILL
CLAREMONT
KARRINYUP
NAVAL BASE
SPEARWO

In [25]:
print(PerthMetro_venues.shape)
PerthMetro_venues.head()

(2107, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  ROTTNEST ISLAND             -32.007488              115.503938   
1  ROTTNEST ISLAND             -32.007488              115.503938   
2          YANCHEP             -31.546670              115.632045   
3          YANCHEP             -31.546670              115.632045   
4          YANCHEP             -31.546670              115.632045   

                    Venue  Venue Latitude  Venue Longitude  Venue Category  
0     Rottnest Lighthouse      -32.007252       115.504441      Lighthouse  
1           Quokka's Nest      -32.007406       115.507211  Scenic Lookout  
2   Daniel's Shagging Pad      -31.546403       115.629235     Yoga Studio  
3  Alkimos Plumbing & Gas      -31.546987       115.634944    Home Service  
4                 Yanchep      -31.547503       115.636485        Pharmacy

In [26]:
PerthMetro_venues.groupby('Venue Category').count()

Neighborhood  Neighborhood Latitude  \
Venue Category                                                       
Airport                                   1                      1   
Airport Terminal                          3                      3   
Amphitheater                              1                      1   
Antique Shop                              2                      2   
Arcade                                    1                      1   
Art Gallery                               3                      3   
Arts & Crafts Store                       3                      3   
Arts & Entertainment                      1                      1   
Asian Restaurant                         43                     43   
Astrologer                                1                      1   
Athletics & Sports                        5                      5   
Australian Restaurant                    22                     22   
Auto Dealership                           1                      1   
Auto Garage                               2                      2   
Auto Workshop                             1                      1   
Automotive Shop                           1                      1   
BBQ Joint                                 3                      3   
Bagel Shop                                1                      1   
Bakery                                   32                     32   
Bar                                      28                     28   
Baseball Field                            1                      1   
Basketball Court                          3                      3   
Beach                                    16                     16   
Beach Bar                                 1                      1   
Bed & Breakfast                           1                      1   
Beer Bar                                  1                      1   
Beer Garden                               5                      5   
Beer Store                                1                      1   
Big Box Store                             8                      8   
Bistro                                    1                      1   
Boat or Ferry                             3                      3   
Bookstore                                 6                      6   
Boutique                                  1                      1   
Bowling Alley                             1                      1   
Bowling Green                             1                      1   
Brazilian Restaurant                      1                      1   
Breakfast Spot                            7                      7   
Brewery                                   4                      4   
Bridge                                    1                      1   
Bubble Tea Shop                           6                      6   
Burger Joint                             20                     20   
Burrito Place                             2                      2   
Bus Station                               5                      5   
Bus Stop                                  8                      8   
Business Service                          7                      7   
Café                                    208                    208   
Campground                                1                      1   
Cantonese Restaurant                      1                      1   
Child Care Service                        1                      1   
Chinese Restaurant                       29                     29   
Chiropractor                              2                      2   
Chocolate Shop                            1                      1   
Climbing Gym                              1                      1   
Clothing Store                           15                     15   
Cocktail Bar                              5                      5   
Coffee Shop                              

In [27]:
print('There are {} uniques categories.'.format(len(PerthMetro_venues['Venue Category'].unique())))

There are 247 uniques categories.


In [28]:
# one hot encoding
Perth_onehot = pd.get_dummies(PerthMetro_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Perth_onehot['Neighborhood'] = PerthMetro_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Perth_onehot.columns[-1]] + list(Perth_onehot.columns[:-1])
Perth_onehot = Perth_onehot[fixed_columns]

Perth_onehot.head(20)

Neighborhood  Airport  Airport Terminal  Amphitheater  Antique Shop  \
0   ROTTNEST ISLAND        0                 0             0             0   
1   ROTTNEST ISLAND        0                 0             0             0   
2           YANCHEP        0                 0             0             0   
3           YANCHEP        0                 0             0             0   
4           YANCHEP        0                 0             0             0   
5        DAWESVILLE        0                 0             0             0   
6          WANNANUP        0                 0             0             0   
7          WANNANUP        0                 0             0             0   
8            FALCON        0                 0             0             0   
9            FALCON        0                 0             0             0   
10           FALCON        0                 0             0             0   
11       HALLS HEAD        0                 0             0             0   
12    GARDEN ISLAND        0                 0             0             0   
13            PERON        0                 0             0             0   
14         MINDARIE        0                 0             0             0   
15         MINDARIE        0                 0             0             0   
16          ERSKINE        0                 0             0             0   
17     QUINNS ROCKS        0                 0             0             0   
18     QUINNS ROCKS        0                 0             0             0   
19     QUINNS ROCKS        0                 0             0             0   

    Arcade  Art Gallery  Arts & Crafts Store  Arts & Entertainment  \
0        0            0                    0                     0   
1        0            0                    0                     0   
2        0            0                    0                     0   
3        0            0                    0                     0   
4        0            0                    0                     0   
5        0            0                    0                     0   
6        0            0                    0                     0   
7        0            0                    0                     0   
8        0            0                    0                     0   
9        0            0                    0                     0   
10       0            0                    0                     0   
11       0            0                    0                     0   
12       0            0                    0                     0   
13       0            0                    0                     0   
14       0            0                    0                     0   
15       0            0                    0                     0   
16       0            0                    0                     0   
17       0            0                    0                     0   
18       0            0                    0                     0   
19       0            0                    0                     0   

    Asian Restaurant  Astrologer  Athletics & Sports  Australian Restaurant  \
0                  0           0                   0                      0   
1                  0           0                   0                      0   
2                  0           0                   0                      0   
3                  0           0                   0                      0   
4                  0           0                   0                      0   
5                  0           0                   0                      0   
6                  0           0                   0                      0   
7                  0           0                   0                      0   
8                  0           0                   0                      0   
9                  0           0                   0                      0   
10                 0        

In [29]:
Perth_onehot.shape

(2107, 248)

In [31]:
Perth_grouped = Perth_onehot.groupby('Neighborhood').mean().reset_index()
Perth_grouped

Neighborhood  Airport  Airport Terminal  Amphitheater  \
0        ALEXANDER HEIGHTS    0.000             0.000          0.00   
1              ALFRED COVE    0.000             0.000          0.00   
2                  ALKIMOS    0.000             0.000          0.00   
3                 ANKETELL    0.000             0.000          0.00   
4               APPLECROSS    0.000             0.000          0.00   
5                  ARDROSS    0.000             0.000          0.00   
6                 ARMADALE    0.000             0.000          0.00   
7                    ASCOT    0.000             0.000          0.00   
8                    ASHBY    0.000             0.000          0.00   
9                 ASHFIELD    0.000             0.000          0.00   
10                ATTADALE    0.000             0.000          0.00   
11                  ATWELL    0.000             0.000          0.00   
12             AUBIN GROVE    0.000             0.000          0.00   
13                  AVELEY    0.000             0.000          0.00   
14                BALCATTA    0.000             0.000          0.00   
15                BALDIVIS    0.000             0.000          0.00   
16                   BALGA    0.000             0.000          0.00   
17               BALLAJURA    0.000             0.000          0.00   
18           BANKSIA GROVE    0.000             0.000          0.00   
19             BASKERVILLE    0.000             0.000          0.00   
20              BASSENDEAN    0.000             0.000          0.00   
21               BAYSWATER    0.000             0.000          0.00   
22            BEACONSFIELD    0.000             0.000          0.00   
23               BECKENHAM    0.000             0.000          0.00   
24                 BEDFORD    0.000             0.000          0.00   
25               BEECHBORO    0.000             0.000          0.00   
26                 BEELIAR    0.000             0.000          0.00   
27                  BELDON    0.000             0.000          0.00   
28                BELLEVUE    0.000             0.000          0.00   
29                 BELMONT    0.000             0.000          0.00   
30                 BENTLEY    0.000             0.000          0.00   
31           BENTLEY SOUTH    0.000             0.000          0.00   
32                 BERTRAM    0.000             0.000          0.00   
33              BIBRA LAKE    0.000             0.000          0.00   
34                  BICTON    0.000             0.000          0.00   
35               BOORAGOON    0.000             0.000          0.00   
36                    BOYA    0.000             0.000          0.00   
37               BRENTWOOD    0.000             0.000          0.00   
38       BROADWAY NEDLANDS    0.000             0.000          0.00   
39               BROOKDALE    0.000             0.000          0.00   
40              BULL CREEK    0.000             0.000          0.00   
41              BULLSBROOK    0.000             0.000          0.00   
42             BURNS BEACH    0.000             0.000          0.00   
43                BURSWOOD    0.000             0.000          0.00   
44                  BUTLER    0.000             0.000          0.00   
45                  BYFORD    0.000             0.000          0.00   
46           CANNING MILLS    0.000             0.000          0.00   
47            CANNING VALE    0.000             0.000          0.00   
48      CANNING VALE SOUTH    0.000             0.000          0.00   
49              CANNINGTON    0.000             0.000          0.00   
50                  CARINE    0.000             0.000          0.00   
51                CARLISLE    0.000             0.000          0.00   
52          CARLISLE NORTH    0.000             0.000          0.00   
53          CARLISLE SOUTH    0.000             0.000          0.00   
54                  CARMEL    0.000             0.000          0.00   
55               CAVERSHAM    0.000   

In [32]:
Perth_grouped.shape

(308, 248)

In [33]:
num_top_venues = 5

for hood in Perth_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Perth_grouped[Perth_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ALEXANDER HEIGHTS----
                     venue  freq
0            Big Box Store  0.33
1                     Park  0.33
2                Gift Shop  0.33
3                  Airport  0.00
4  North Indian Restaurant  0.00


----ALFRED COVE----
               venue  freq
0  Indian Restaurant  0.50
1        Gas Station  0.25
2               Café  0.25
3             Office  0.00
4      Movie Theater  0.00


----ALKIMOS----
               venue  freq
0  Indian Restaurant  0.25
1               Park  0.25
2           Bus Stop  0.25
3      Grocery Store  0.25
4             Office  0.00


----ANKETELL----
         venue  freq
0          Pub  0.33
1  Golf Course  0.33
2   Hobby Shop  0.33
3      Airport  0.00
4  Music Venue  0.00


----APPLECROSS----
                      venue  freq
0        Italian Restaurant  0.08
1                Restaurant  0.08
2              Burger Joint  0.08
3                      Café  0.08
4  Mediterranean Restaurant  0.08


----ARDROSS----
                venue  f

           venue  freq
0    IT Services  0.25
1    Bus Station  0.25
2    Auto Garage  0.25
3  Grocery Store  0.25
4         Office  0.00


----BYFORD----
                  venue  freq
0         Grocery Store  0.25
1                   Pub  0.25
2  Fast Food Restaurant  0.25
3         Shopping Mall  0.25
4               Airport  0.00


----CANNING MILLS----
           venue  freq
0           Park   1.0
1        Airport   0.0
2         Office   0.0
3          Motel   0.0
4  Movie Theater   0.0


----CANNING VALE----
                        venue  freq
0          Seafood Restaurant  0.25
1              Sandwich Place  0.25
2                Home Service  0.25
3  Construction & Landscaping  0.25
4               National Park  0.00


----CANNING VALE SOUTH----
                venue  freq
0   Convenience Store  0.29
1                 Pub  0.14
2  Chinese Restaurant  0.14
3      Sandwich Place  0.14
4      Farmers Market  0.14


----CANNINGTON----
                  venue  freq
0  Fast Food Res

          venue  freq
0   Pizza Place  0.29
1           Gym  0.14
2           Bar  0.14
3           Pub  0.14
4  Burger Joint  0.14


----EDGEWATER----
           venue  freq
0           Park   1.0
1        Airport   0.0
2         Office   0.0
3          Motel   0.0
4  Movie Theater   0.0


----EGLINTON----
                  venue  freq
0  Gym / Fitness Center   1.0
1     Other Repair Shop   0.0
2                 Motel   0.0
3         Movie Theater   0.0
4         Moving Target   0.0


----ELLENBROOK----
                venue  freq
0                Park  0.29
1   Fish & Chips Shop  0.14
2  Chinese Restaurant  0.14
3     Thai Restaurant  0.14
4       Shopping Mall  0.14


----EMBLETON----
                     venue  freq
0     Fast Food Restaurant  0.67
1             Soccer Field  0.33
2                  Airport  0.00
3  North Indian Restaurant  0.00
4                    Motel  0.00


----ERSKINE----
               venue  freq
0             Resort   1.0
1            Airport   0.0
2  Oth

              venue  freq
0       Coffee Shop  0.08
1              Café  0.08
2       Supermarket  0.06
3  Department Store  0.06
4      Burger Joint  0.06


----JOONDANNA----
               venue  freq
0                Bar  0.33
1  Convenience Store  0.33
2               Park  0.33
3            Airport  0.00
4      National Park  0.00


----KALAMUNDA----
            venue  freq
0            Café   0.3
1  Farmers Market   0.1
2             Pub   0.1
3     Supermarket   0.1
4   Shopping Mall   0.1


----KALLAROO----
                        venue  freq
0  Construction & Landscaping  0.33
1           Fish & Chips Shop  0.33
2                        Park  0.33
3                     Airport  0.00
4                      Office  0.00


----KARAWARA----
                  venue  freq
0  Fast Food Restaurant  0.10
1   Japanese Restaurant  0.05
2         Shopping Mall  0.05
3              Tea Room  0.05
4           Supermarket  0.05


----KARDINYA----
                       venue  freq
0         

               venue  freq
0               Café  0.33
1  Fish & Chips Shop  0.17
2               Park  0.17
3       Liquor Store  0.17
4      Grocery Store  0.17


----MENORA----
               venue  freq
0        Beer Garden  0.14
1  College Cafeteria  0.14
2               Park  0.14
3       Tennis Court  0.14
4           Bus Stop  0.14


----MERRIWA----
           venue  freq
0     Playground  0.25
1  Shopping Mall  0.25
2   Liquor Store  0.25
3         Bakery  0.25
4        Airport  0.00


----MIDDLE SWAN----
           venue  freq
0  Bowling Green   0.5
1       Pharmacy   0.5
2        Airport   0.0
3         Office   0.0
4          Motel   0.0


----MIDLAND----
                 venue  freq
0                 Café  0.14
1  Japanese Restaurant  0.14
2              Brewery  0.07
3     Asian Restaurant  0.07
4        Shopping Mall  0.07


----MIDVALE----
               venue  freq
0           Bus Stop   0.5
1               Café   0.5
2            Airport   0.0
3  Other Repair Shop   0.

                  venue  freq
0           Coffee Shop  0.11
1          Tennis Court  0.11
2                Bakery  0.11
3  Outdoor Supply Store  0.11
4     Electronics Store  0.11


----PERON----
               venue  freq
0    Harbor / Marina   1.0
1            Airport   0.0
2  Other Repair Shop   0.0
3              Motel   0.0
4      Movie Theater   0.0


----PERTH----
                     venue  freq
0              Sports Club  0.25
1              Pizza Place  0.25
2      Rental Car Location  0.25
3             Liquor Store  0.25
4  North Indian Restaurant  0.00


----PERTH ADELAIDE TCE----
              venue  freq
0              Café  0.16
1             Hotel  0.13
2  Asian Restaurant  0.08
3    Sandwich Place  0.05
4       Coffee Shop  0.05


----PERTH AIRPORT----
                venue  freq
0    Airport Terminal  0.38
1                Café  0.12
2  Miscellaneous Shop  0.12
3                 Pub  0.12
4      Sandwich Place  0.12


----PERTH ST GEORGES TCE----
                   v

                venue  freq
0  Seafood Restaurant  0.33
1                Park  0.33
2                Café  0.17
3               Beach  0.17
4        Night Market  0.00


----TUART HILL----
                  venue  freq
0    Italian Restaurant  0.25
1              Pharmacy  0.19
2  Fast Food Restaurant  0.19
3         Grocery Store  0.19
4    Mexican Restaurant  0.06


----VICTORIA PARK----
                 venue  freq
0          Pizza Place  0.12
1                 Café  0.12
2  Japanese Restaurant  0.08
3                  Pub  0.04
4      Thai Restaurant  0.04


----VIVEASH----
                venue  freq
0  Photography Studio   1.0
1             Airport   0.0
2              Office   0.0
3               Motel   0.0
4       Movie Theater   0.0


----WAIKIKI----
                  venue  freq
0   Sporting Goods Shop   0.2
1           Supermarket   0.2
2     Convenience Store   0.2
3  Fast Food Restaurant   0.2
4         Shopping Mall   0.2


----WALLISTON----
               venue  freq
0 

In [34]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [35]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Perth_grouped['Neighborhood']

for ind in np.arange(Perth_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Perth_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  ALEXANDER HEIGHTS         Big Box Store                  Park   
1        ALFRED COVE     Indian Restaurant                  Café   
2            ALKIMOS         Grocery Store              Bus Stop   
3           ANKETELL           Golf Course                   Pub   
4         APPLECROSS                 Beach            Restaurant   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0             Gift Shop           Yoga Studio            Electronics Store   
1           Gas Station           Yoga Studio            Food & Drink Shop   
2     Indian Restaurant                  Park                  Yoga Studio   
3            Hobby Shop                  Farm  Eastern European Restaurant   
4  Cantonese Restaurant          Burger Joint               Ice Cream Shop   

  6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
0     Food & Drink Shop                      Food           Flower Shop   
1                  Food               Flower Shop           Flea Market   
2                  Farm             Event Service            Eye Doctor   
3     Electronics Store             Event Service            Eye Doctor   
4   Hawaiian Restaurant  Mediterranean Restaurant    Italian Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Flea Market      Fish & Chips Shop  
1     Fish & Chips Shop   Fast Food Restaurant  
2    Falafel Restaurant         Farmers Market  
3    Falafel Restaurant            Yoga Studio  
4   Japanese Restaurant                 Lounge

## Cluster Perth, Neighborhoods

In [36]:
# number of clusters
kclusters = 5

Perth_grouped_clustering = Perth_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Perth_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([4, 2, 1, 1, 1, 1, 1, 3, 4, 1], dtype=int32)

#### 
Lakshmi hollaTeaching Staff · 2 hours ago
Hello Christopher,

Thanks for your post.We are happy to assist you.

The cluster labels are created already when you run the cell for the first time.

In the second execution it will throw this error.

Comment on the line

# neighborh00d_sorted.insert(0,'Cluster_labels') and then execute the cell.

Hope this helps.

With Regards

Lakshmi Holla

In [37]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Perth_merged = df_Perth_West


Perth_merged = Perth_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood', how = 'inner')

Perth_merged.head()

postcode     Neighborhood            dc        lat         lon  \
0      6161  ROTTNEST ISLAND    PALMYRA DC -32.007488  115.503938   
1      6035          YANCHEP  JOONDALUP DC -31.546670  115.632045   
2      6211       DAWESVILLE   MANDURAH DC -32.634691  115.634411   
3      6210         WANNANUP   MANDURAH DC -32.598055  115.643883   
4      6210           FALCON   MANDURAH DC -32.589738  115.647291   

   Cluster Labels 1st Most Common Venue       2nd Most Common Venue  \
0               1        Scenic Lookout                  Lighthouse   
1               1           Yoga Studio                Home Service   
2               1           Yoga Studio                Food Service   
3               1         Boat or Ferry                         Pub   
4               1                 Beach  Construction & Landscaping   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
0   Dumpling Restaurant                         Food           Flower Shop   
1              Pharmacy          Dumpling Restaurant                  Food   
2     Food & Drink Shop                         Food           Flower Shop   
3   Dumpling Restaurant            Food & Drink Shop                  Food   
4           Yoga Studio  Eastern European Restaurant     Food & Drink Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Flea Market     Fish & Chips Shop  Fast Food Restaurant   
1           Flower Shop           Flea Market     Fish & Chips Shop   
2           Flea Market     Fish & Chips Shop  Fast Food Restaurant   
3           Flower Shop           Flea Market     Fish & Chips Shop   
4                  Food           Flower Shop           Flea Market   

  9th Most Common Venue 10th Most Common Venue  
0        Farmers Market                   Farm  
1  Fast Food Restaurant         Farmers Market  
2        Farmers Market                   Farm  
3  Fast Food Restaurant         Farmers Market  
4     Fish & Chips Shop   Fast Food Restaurant

In [38]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Perth_merged['lat'], Perth_merged['lon'], Perth_merged['Neighborhood'], Perth_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Cluster 1 Red Cluster

In [39]:
Perth_merged.loc[Perth_merged['Cluster Labels'] == 0, Perth_merged.columns[[1] + list(range(5, Perth_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
24      MANDURAH               0          Home Service           Yoga Studio   
203    LAKELANDS               0          Home Service           Yoga Studio   
212     GNANGARA               0          Home Service           Yoga Studio   
216    NAMBEELUP               0          Home Service           Yoga Studio   
228        WANDI               0          Home Service           Yoga Studio   
359         BOYA               0          Home Service           Yoga Studio   
368       CARMEL               0                Winery          Home Service   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
24    Dumpling Restaurant     Food & Drink Shop                  Food   
203   Dumpling Restaurant     Food & Drink Shop                  Food   
212   Dumpling Restaurant     Food & Drink Shop                  Food   
216   Dumpling Restaurant     Food & Drink Shop                  Food   
228   Dumpling Restaurant     Food & Drink Shop                  Food   
359   Dumpling Restaurant     Food & Drink Shop                  Food   
368           Yoga Studio        Farmers Market     Electronics Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
24            Flower Shop           Flea Market     Fish & Chips Shop   
203           Flower Shop           Flea Market     Fish & Chips Shop   
212           Flower Shop           Flea Market     Fish & Chips Shop   
216           Flower Shop           Flea Market     Fish & Chips Shop   
228           Flower Shop           Flea Market     Fish & Chips Shop   
359           Flower Shop           Flea Market     Fish & Chips Shop   
368         Event Service            Eye Doctor    Falafel Restaurant   

    9th Most Common Venue 10th Most Common Venue  
24   Fast Food Restaurant         Farmers Market  
203  Fast Food Restaurant         Farmers Market  
212  Fast Food Restaurant         Farmers Market  
216  Fast Food Restaurant         Farmers Market  
228  Fast Food Restaurant         Farmers Market  
359  Fast Food Restaurant         Farmers Market  
368                  Farm      Fish & Chips Shop

## Cluster 2 Purple Cluster

In [40]:
Perth_merged.loc[Perth_merged['Cluster Labels'] == 1, Perth_merged.columns[[1] + list(range(5, Perth_merged.shape[1]))]]

Neighborhood  Cluster Labels       1st Most Common Venue  \
0         ROTTNEST ISLAND               1              Scenic Lookout   
1                 YANCHEP               1                 Yoga Studio   
2              DAWESVILLE               1                 Yoga Studio   
3                WANNANUP               1               Boat or Ferry   
4                  FALCON               1                       Beach   
5              HALLS HEAD               1                 Flea Market   
8                   PERON               1             Harbor / Marina   
9                MINDARIE               1                       Trail   
10                ERSKINE               1                      Resort   
12                 BUTLER               1               Grocery Store   
13             SHOALWATER               1           Electronics Store   
14             SAFETY BAY               1          Mexican Restaurant   
15                MERRIWA               1                  Playground   
20                ALKIMOS               1               Grocery Store   
26             OCEAN REEF               1                 Pizza Place   
29         MANDURAH NORTH               1      Furniture / Home Store   
30          MANDURAH EAST               1      Furniture / Home Store   
31               HILLARYS               1                      Bakery   
32               MULLALOO               1               Grocery Store   
36             ROCKINGHAM               1                        Café   
38               CONNOLLY               1               Shopping Mall   
39               SORRENTO               1                    Bus Stop   
44                MARMION               1                       Beach   
45             MADORA BAY               1                  Astrologer   
46               COODANUP               1           Electronics Store   
47        NORTH FREMANTLE               1                       Beach   
48            NORTH BEACH               1                       Beach   
51             CITY BEACH               1                       Beach   
53                WARNBRO               1        Gym / Fitness Center   
54                 BELDON               1                Home Service   
55              SINGLETON               1                        Park   
56            MOSMAN PARK               1                 Coffee Shop   
57        SOUTH FREMANTLE               1                 Supermarket   
59            GREENFIELDS               1     Health & Beauty Service   
60            SCARBOROUGH               1          Italian Restaurant   
61            NORTH PERTH               1               Deli / Bodega   
62        CLAREMONT NORTH               1               Deli / Bodega   
63             COOLOONGUP               1                  Steakhouse   
64              COTTESLOE               1                        Café   
65             HEATHRIDGE               1                 Pizza Place   
70       PEPPERMINT GROVE               1               Shopping Mall   
71       WHITE GUM VALLEY               1                 Pizza Place   
73                CRAIGIE               1               Grocery Store   
74              JOONDALUP               1                 Coffee Shop   
75                HILLMAN               1                   Pet Store   
77             SWANBOURNE               1                   Bookstore   
80          WEMBLEY DOWNS               1                      Bakery   
81                PALMYRA               1                        Café   
82          KWINANA BEACH               1                        Farm   
84                 CARINE               1          Athletics & Sports   
89              CLAREMONT               1                        Café   
90              KARRINYUP               1            Department Store   
91             NAVAL BASE               1  Construction & Landscaping   
95               WOODVALE               1                 Pizza Place  

## Cluster 3 Blue Cluster

In [41]:
Perth_merged.loc[Perth_merged['Cluster Labels'] == 2, Perth_merged.columns[[1] + list(range(5, Perth_merged.shape[1]))]]

Neighborhood  Cluster Labels      1st Most Common Venue  \
11            QUINNS ROCKS               2                       Café   
23        ROCKINGHAM BEACH               2                       Café   
58          EAST FREMANTLE               2                       Café   
66            BEACONSFIELD               2             Farmers Market   
67               FREMANTLE               2                       Café   
68                  COOGEE               2                 Campground   
69                DUNCRAIG               2             Breakfast Spot   
76               HENDERSON               2             Scenic Lookout   
85         MOUNT CLAREMONT               2                       Park   
86              DOUBLEVIEW               2           Asian Restaurant   
93                  BICTON               2                       Café   
104         SOUTH YUNDERUP               2                       Café   
112               DALKEITH               2                       Café   
118               MELVILLE               2                       Café   
129            ALFRED COVE               2          Indian Restaurant   
132               NEDLANDS               2                       Café   
134               HERDSMAN               2     Furniture / Home Store   
135           OSBORNE PARK               2                       Café   
138               KARDINYA               2                       Café   
162       WEST LEEDERVILLE               2                       Café   
176            LEEDERVILLE               2                       Café   
180             WEST PERTH               2                       Café   
191              BRENTWOOD               2                       Café   
194         MOUNT PLEASANT               2                       Café   
199              COOLBINIA               2                       Café   
207  SOUTH PERTH ANGELO ST               2                       Café   
208            SOUTH PERTH               2                       Café   
215          BENTLEY SOUTH               2                       Café   
217                MANNING               2                       Café   
219                   COMO               2                Pizza Place   
222              ROSSMOYNE               2                Pizza Place   
225              LANDSDALE               2                       Café   
230             KENSINGTON               2                 Playground   
232              INGLEWOOD               2                       Café   
233                SHELLEY               2                       Café   
238               MAYLANDS               2                       Café   
242              BAYSWATER               2                       Café   
259              BAYSWATER               2                       Café   
255               LATHLAIN               2                       Café   
285               WHITEMAN               2                       Café   
292            QUEENS PARK               2  Middle Eastern Restaurant   
335             HERNE HILL               2                       Café   
340                MIDVALE               2                       Café   
354        GOOSEBERRY HILL               2                Pizza Place   
360              KALAMUNDA               2                       Café   
365             ROLEYSTONE               2                       Café   
367             DARLINGTON               2                       Café   
373           GLEN FORREST               2                       Café   
381              MUNDARING               2                       Café   

          2nd Most Common Venue  3rd Most Common Venue  \
11                Shopping Mall                 Bakery   
23        Australian Restaurant       Tapas Restaurant   
58                  Art Gallery            Gas Station   
66                   Restaurant                   Café   
67                  Yoga Studio      Food & Drink Shop   
68             

## Cluster 4 Green Cluster

In [42]:
Perth_merged.loc[Perth_merged['Cluster Labels'] == 3, Perth_merged.columns[[1] + list(range(5, Perth_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
16           BURNS BEACH               3            Playground   
18              CLARKSON               3          Liquor Store   
21           DUDLEY PARK               3  Fast Food Restaurant   
43        MEADOW SPRINGS               3          Gourmet Shop   
50          PORT KENNEDY               3          Food Service   
52               WAIKIKI               3     Convenience Store   
72               PADBURY               3           Pizza Place   
88         HAMILTON HILL               3         Grocery Store   
92             SPEARWOOD               3  Fast Food Restaurant   
97               MUNSTER               3           Pizza Place   
98              KINGSLEY               3  Fast Food Restaurant   
123             WANNEROO               3  Fast Food Restaurant   
128              WARWICK               3  Fast Food Restaurant   
131             STIRLING               3                  Café   
136             JOLIMONT               3  Fast Food Restaurant   
139  KWINANA TOWN CENTRE               3        Sandwich Place   
144     WILLAGEE CENTRAL               3                  Park   
151             BALDIVIS               3  Fast Food Restaurant   
156          WESTMINSTER               3         Shopping Mall   
157           SOUTH LAKE               3           Supermarket   
160           GIRRAWHEEN               3  Fast Food Restaurant   
183            DOG SWAMP               3           Supermarket   
189              BERTRAM               3         Grocery Store   
201           BULL CREEK               3  Fast Food Restaurant   
205             DIANELLA               3           Pizza Place   
224             PINJARRA               3        Sandwich Place   
241               MALAGA               3          Dance Studio   
243              NORANDA               3                  Café   
256                PERTH               3           Pizza Place   
264             EMBLETON               3  Fast Food Restaurant   
269           BASSENDEAN               3           Supermarket   
291           BASSENDEAN               3           Supermarket   
272                ASCOT               3  Fast Food Restaurant   
274            BEECHBORO               3  Fast Food Restaurant   
283           CANNINGTON               3  Fast Food Restaurant   
305            CAVERSHAM               3     Convenience Store   
318        SEVILLE GROVE               3        Sandwich Place   
323             GOSNELLS               3  Fast Food Restaurant   
325               BYFORD               3         Grocery Store   
326               AVELEY               3     Convenience Store   
331         FORRESTFIELD               3  Fast Food Restaurant   
333         HIGH WYCOMBE               3           Pizza Place   
334            KELMSCOTT               3  Fast Food Restaurant   

     2nd Most Common Venue       3rd Most Common Venue  \
16    Fast Food Restaurant                       Beach   
18             Pizza Place                        Park   
21             Yoga Studio                Food Service   
43    Fast Food Restaurant              Clothing Store   
50        Department Store        Fast Food Restaurant   
52           Shopping Mall                 Supermarket   
72           Grocery Store                Liquor Store   
88                    Food                    Pharmacy   
92             Pizza Place                 Supermarket   
97             Yoga Studio         Dumpling Restaurant   
98       Convenience Store                Liquor Store   
123                   Café            Department Store   
128            Supermarket                        Café   
131            Pizza Place        Fast Food Restaurant   
136      Convenience Store                         Gym   
139            Supermarket                Liquor Store   
144      Indian Restaurant                 Sports Club   
151           Liquor Store            Department Store   
156  

## Cluster 5 Orange Cluster

In [43]:
Perth_merged.loc[Perth_merged['Cluster Labels'] == 4, Perth_merged.columns[[1] + list(range(5, Perth_merged.shape[1]))]]

Neighborhood  Cluster Labels       1st Most Common Venue  \
7        GARDEN ISLAND               4                        Park   
22               ILUKA               4                        Park   
27             KINROSS               4                  Playground   
34          CURRAMBINE               4                        Park   
35            KALLAROO               4  Construction & Landscaping   
42     EAST ROCKINGHAM               4                       Beach   
49               TRIGG               4          Seafood Restaurant   
94           EDGEWATER               4                        Park   
96         CHURCHLANDS               4                        Park   
101            INNALOO               4                        Park   
103              ASHBY               4                        Park   
115             SAMSON               4                        Park   
119          HAMERSLEY               4                        Park   
127         COOLBELLUP               4                        Park   
140        GLENDALOUGH               4                        Park   
143      BANKSIA GROVE               4                        Park   
150             ORELIA               4                        Park   
152            BEELIAR               4                  Smoke Shop   
172          JOONDANNA               4           Convenience Store   
173         MARANGAROO               4                   Gift Shop   
192       HAMMOND PARK               4                        Park   
193           KINGSWAY               4                        Park   
210            LEEMING               4                        Park   
214  ALEXANDER HEIGHTS               4               Big Box Store   
226         EAST PERTH               4                        Park   
237          BALLAJURA               4                        Pool   
239          PARKLANDS               4           Convenience Store   
240            BEDFORD               4                        Park   
288          LOCKRIDGE               4                        Park   
297        HUNTINGDALE               4                        Park   
301         ELLENBROOK               4                        Park   
306         SERPENTINE               4                        Park   
311          MUNDIJONG               4                        Park   
321          THE VINES               4                  Playground   
348          KOONGAMIA               4                        Park   
353         JANE BROOK               4                        Park   
375      CANNING MILLS               4                        Park   

    2nd Most Common Venue  3rd Most Common Venue        4th Most Common Venue  \
7             Yoga Studio    Dumpling Restaurant            Food & Drink Shop   
22                 Market            Yoga Studio          Dumpling Restaurant   
27                   Park          Shopping Mall                  Dry Cleaner   
34           Home Service            Yoga Studio          Dumpling Restaurant   
35      Fish & Chips Shop                   Park                  Yoga Studio   
42                   Park            Yoga Studio  Eastern European Restaurant   
49                   Park                   Café                        Beach   
94            Yoga Studio    Dumpling Restaurant            Food & Drink Shop   
96           Home Service     Athletics & Sports                  Yoga Studio   
101                   Pub           Liquor Store                Grocery Store   
103           Yoga Studio    Dumpling Restaurant            Food & Drink Shop   
115      Basketball Court            Yoga Studio  Eastern European Restaurant   
119  Gym / Fitness Center            Yoga Studio          Dumpling Restaurant   
127         Grocery Store   Fast Food Restaurant                 Liquor Store   
140      Business Service            Pizza Place                  Yoga Studio   
143           Yoga Studio    Dumpling Restaurant     

## Calculating distance from CBD to each suburb Latitude and longitude values of CITY DELIVERY CENTRE are -31.95505, 115.857527.

In [16]:
pip install haversine

/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-main/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
Note: you may need to restart the kernel to use updated packages.


In [17]:
import haversine as hs

In [25]:
loc1=(-31.546670,115.632045) # yanchep
loc2=(-32.634691,115.634411) # dawesville
hs.haversine(loc1, loc2)

120.9827876957157

### The above haversine calculation 20015.114442035923 KM is halfway around the world at the equater, the actual figure for the circumfernce of the earth at the equater is 40,075.017 km. The main discrepancy probably is that the earth is not a perfect circle. The difference is 0.1118 % [Haversine](https://en.wikipedia.org/wiki/Haversine_formula)


In [20]:
def haversine_distance(lat1, lon1, lat2, lon2):
   r = 6371
   phi1 = np.radians(lat1)
   phi2 = np.radians(lat2)
   delta_phi = np.radians(lat2-lat1)
   delta_lambda = np.radians(lon2-lon1)
   a = np.sin(delta_phi / 2)**2 + np.cos(phi1) * np.cos(phi2) *   np.sin(delta_lambda / 2)**2
   res = r * (2 * np.arctan2(np.sqrt(a), np.sqrt(1-a)))
   return np.round(res, 2)

In [22]:
df_Perth_LL = df_Perth_West.sort_values('lat')

NameError: name 'df_Perth_West' is not defined

In [21]:
start_lat = -31.95505
start_lon = 115.857527

distances_km = []
for row in df_Perth_LL.itertuples(index=False):
   distances_km.append(
       haversine_distance(start_lat, start_lon, row.lat, row.lon)
   )

df_Perth_LL['DistanceFromCBD_KM'] = distances_km
df_Perth_LL.head()

NameError: name 'df_Perth_LL' is not defined

In [50]:
df_Perth_LL.head(50)

postcode    Neighborhood             dc        lat         lon  \
2        6211      DAWESVILLE    MANDURAH DC -32.634691  115.634411   
87       6208         NIRIMBA    MANDURAH DC -32.633742  115.779033   
224      6208        PINJARRA    MANDURAH DC -32.628562  115.875029   
369      6213     BANKSIADALE    MANDURAH DC -32.623155  116.084814   
271      6208          OAKLEY    MANDURAH DC -32.617084  115.922708   
3        6210        WANNANUP    MANDURAH DC -32.598055  115.643883   
275      6208      FAIRBRIDGE    MANDURAH DC -32.596708  115.925936   
4        6210          FALCON    MANDURAH DC -32.589738  115.647291   
104      6208  SOUTH YUNDERUP    MANDURAH DC -32.585445  115.793317   
99       6208  NORTH YUNDERUP    MANDURAH DC -32.575937  115.791844   
227      6208      RAVENSWOOD    MANDURAH DC -32.561246  115.878117   
78       6209     FURNISSDALE    MANDURAH DC -32.561118  115.771132   
10       6210         ERSKINE    MANDURAH DC -32.557169  115.706571   
356      6207       WHITTAKER    MANDURAH DC -32.551110  116.050830   
46       6210        COODANUP    MANDURAH DC -32.550988  115.751804   
5        6210      HALLS HEAD    MANDURAH DC -32.549355  115.682764   
21       6210     DUDLEY PARK    MANDURAH DC -32.540594  115.725353   
24       6210        MANDURAH    MANDURAH DC -32.533010  115.732537   
59       6210     GREENFIELDS    MANDURAH DC -32.520075  115.758778   
298      6207  NORTH DANDALUP    MANDURAH DC -32.519317  115.971299   
29       6210  MANDURAH NORTH    MANDURAH DC -32.515318  115.741060   
30       6210   MANDURAH EAST    MANDURAH DC -32.515318  115.741060   
25       6210    SILVER SANDS    MANDURAH DC -32.510602  115.732823   
216      6207       NAMBEELUP    MANDURAH DC -32.507220  115.868060   
43       6210  MEADOW SPRINGS    MANDURAH DC -32.494802  115.751392   
33       6210        SAN REMO    MANDURAH DC -32.488900  115.743998   
363      6207           MYARA    MANDURAH DC -32.487206  116.068209   
45       6210      MADORA BAY    MANDURAH DC -32.465347  115.751528   
55       6175       SINGLETON    MANDURAH DC -32.445807  115.757022   
304      6126       KEYSBROOK   KELMSCOTT DC -32.440033  115.977043   
41       6174      GOLDEN BAY    MANDURAH DC -32.429853  115.750353   
40       6173  SECRET HARBOUR    MANDURAH DC -32.402574  115.749186   
50       6172    PORT KENNEDY  ROCKINGHAM DC -32.375470  115.753147   
246      6125        HOPELAND   KELMSCOTT DC -32.364427  115.901277   
254      6176          KARNUP  ROCKINGHAM DC -32.364374  115.909164   
306      6125      SERPENTINE   KELMSCOTT DC -32.363879  115.980218   
53       6169         WARNBRO  ROCKINGHAM DC -32.344007  115.755943   
366      6124      JARRAHDALE   KELMSCOTT DC -32.338316  116.072494   
151      6171        BALDIVIS  ROCKINGHAM DC -32.331964  115.821549   
307      6125        MARDELLA   KELMSCOTT DC -32.331865  115.980909   
52       6169         WAIKIKI  ROCKINGHAM DC -32.314919  115.754810   
14       6169      SAFETY BAY  ROCKINGHAM DC -32.303433  115.711289   
63       6168      COOLOONGUP  ROCKINGHAM DC -32.299743  115.762751   
330      6123          WHITBY   KELMSCOTT DC -32.295719  116.010451   
13       6169      SHOALWATER  ROCKINGHAM DC -32.295540  115.710646   
311      6123       MUNDIJONG   KELMSCOTT DC -32.295176  115.985890   
20       6038         ALKIMOS   JOONDALUP DC -32.289149  115.723047   
36       6168      ROCKINGHAM  ROCKINGHAM DC -32.288048  115.745967   
75       6168         HILLMAN  ROCKINGHAM DC -32.280685  115.769932   
8        6168           PERON  ROCKINGHAM DC -32.278879  115.703147   

     DistanceFromCBD_KM  
2                 78.43  
87                75.83  
224               74.91  
369               77.30  
271               73.87  
3                 74.27  
275               71.64  
4                 73.29  
104               70.36  
99                69.32  
227               67.43  
78                67.88  
10                68.44  
356               6

## Test Data for Haversine

In [23]:
df_LTLO_test = pd.DataFrame(
{"lat" : [0, 180],
"lon" : [180, 0]},
index = [0, 1])
df_LTLO_test

lat  lon
0    0  180
1  180    0

In [24]:
start_lat = 0
start_lon = 0

distances_km = []
for row in df_LTLO_test.itertuples(index=False):
   distances_km.append(
       haversine_distance(start_lat, start_lon, row.lat, row.lon)
   )

df_LTLO_test['Distance_Half_Earth_KM'] = distances_km
df_LTLO_test.head()

lat  lon  Distance_Half_Earth_KM
0    0  180                20015.09
1  180    0                20015.09

#### The above data is the correct result the havesine function program works

## Perth Housing data from a random sample of the above data frame n = 80

In [60]:

body = client_23e3b5aeac9043948fc832b12320c85a.get_object(Bucket='ibmdscapstoneweel3toronto-donotdelete-pr-uew1iz4itwgorw',Key='Western_Australia_Post_Geo_House.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_data_6 = pd.read_csv(body)
df_data_6.head()


postcode          suburb state             dc  \
0      6208  NORTH YUNDERUP    WA    MANDURAH DC   
1      6210     GREENFIELDS    WA    MANDURAH DC   
2      6173  SECRET HARBOUR    WA    MANDURAH DC   
3      6172    PORT KENNEDY    WA  ROCKINGHAM DC   
4      6125      SERPENTINE    WA   KELMSCOTT DC   

                                            type        lat         lon  \
0  Delivery Area                                 -32.575937  115.791844   
1  Delivery Area                                 -32.520075  115.758778   
2  Delivery Area                                 -32.402574  115.749186   
3  Delivery Area                                 -32.375470  115.753147   
4  Delivery Area                                 -32.363879  115.980218   

   Median_House_Price  North_South  
0              510000            1  
1              298000            1  
2              463750            1  
3              370000            1  
4              667500            1

In [63]:
df_Perth_House = df_data_6.sort_values('lat')

In [64]:
start_lat = -31.95505
start_lon = 115.857527

distances_km = []
for row in df_Perth_House.itertuples(index=False):
   distances_km.append(
       haversine_distance(start_lat, start_lon, row.lat, row.lon)
   )

df_Perth_House['DistanceFromCBD_KM'] = distances_km
df_Perth_House.head()

postcode          suburb state             dc  \
0      6208  NORTH YUNDERUP    WA    MANDURAH DC   
1      6210     GREENFIELDS    WA    MANDURAH DC   
2      6173  SECRET HARBOUR    WA    MANDURAH DC   
3      6172    PORT KENNEDY    WA  ROCKINGHAM DC   
4      6125      SERPENTINE    WA   KELMSCOTT DC   

                                            type        lat         lon  \
0  Delivery Area                                 -32.575937  115.791844   
1  Delivery Area                                 -32.520075  115.758778   
2  Delivery Area                                 -32.402574  115.749186   
3  Delivery Area                                 -32.375470  115.753147   
4  Delivery Area                                 -32.363879  115.980218   

   Median_House_Price  North_South  DistanceFromCBD_KM  
0              510000            1               69.32  
1              298000            1               63.51  
2              463750            1               50.80  
3              370000            1               47.77  
4              667500            1               46.90

In [65]:
start_lon = 115.730352 # (Rockingham beach) this longitude is used to approximate the coast
# calcualte distance between 2 longitude points at the same, latitude
distances_km = []
for row in df_Perth_House.itertuples(index=False):
   distances_km.append(
       haversine_distance(row.lat, start_lon, row.lat, row.lon)
   )

df_Perth_House['DistanceFromCoast'] = distances_km
df_Perth_House

postcode                 suburb state                    dc  \
0       6208         NORTH YUNDERUP    WA           MANDURAH DC   
1       6210            GREENFIELDS    WA           MANDURAH DC   
2       6173         SECRET HARBOUR    WA           MANDURAH DC   
3       6172           PORT KENNEDY    WA         ROCKINGHAM DC   
4       6125             SERPENTINE    WA          KELMSCOTT DC   
5       6169                WARNBRO    WA         ROCKINGHAM DC   
6       6171               BALDIVIS    WA         ROCKINGHAM DC   
7       6169                WAIKIKI    WA         ROCKINGHAM DC   
8       6168             COOLOONGUP    WA         ROCKINGHAM DC   
9       6123                 WHITBY    WA          KELMSCOTT DC   
10      6122                 CARDUP    WA          KELMSCOTT DC   
11      6167              CASUARINA    WA         ROCKINGHAM DC   
12      6121                OAKFORD    WA          KELMSCOTT DC   
13      6167                  WANDI    WA         ROCKINGHAM DC   
14      6112           MOUNT RICHON    WA          KELMSCOTT DC   
15      6112           MOUNT NASURA    WA          KELMSCOTT DC   
16      6112          SEVILLE GROVE    WA          KELMSCOTT DC   
17      6111              KELMSCOTT    WA          KELMSCOTT DC   
18      6164             SOUTH LAKE    WA         BIBRA LAKE DC   
19      6163              SPEARWOOD    WA         BIBRA LAKE DC   
20      6110            HUNTINGDALE    WA          KELMSCOTT DC   
21      6155     CANNING VALE SOUTH    WA       CANNING VALE DC   
22      6162           BEACONSFIELD    WA            PALMYRA DC   
23      6156               WILLAGEE    WA            PALMYRA DC   
24      6109             MADDINGTON    WA          KELMSCOTT DC   
25      6153              BRENTWOOD    WA            PALMYRA DC   
26      6147               PARKWOOD    WA       CANNING VALE DC   
27      6157                PALMYRA    WA            PALMYRA DC   
28      6154              BOORAGOON    WA            PALMYRA DC   
29      6160              FREMANTLE    WA            PALMYRA DC   
30      6153         MOUNT PLEASANT    WA            PALMYRA DC   
31      6153             APPLECROSS    WA            PALMYRA DC   
32      6152               KARAWARA    WA            BENTLEY DC   
33      6107        EAST CANNINGTON    WA          WELSHPOOL DC   
34      5000              WALLISTON    WA          WALLISTON DC   
35      6076              LESMURDIE    WA          WALLISTON DC   
36      6011              COTTESLOE    WA           NEDLANDS DC   
37      6102          BENTLEY SOUTH    WA            BENTLEY DC   
38      6058           FORRESTFIELD    WA          WELSHPOOL DC   
39      6006            NORTH PERTH    WA         BASSENDEAN DC   
40      6010              CLAREMONT    WA           NEDLANDS DC   
41      6151  SOUTH PERTH ANGELO ST    WA            BENTLEY DC   
42      6101               CARLISLE    WA            BENTLEY DC   
43      6076              KALAMUNDA    WA          WALLISTON DC   
44      6164       COCKBURN CENTRAL    WA         BIBRA LAKE DC   
45      6105             CLOVERDALE    WA          WELSHPOOL DC   
46      6008           SHENTON PARK    WA           NEDLANDS DC   
47      6076        GOOSEBERRY HILL    WA          WALLISTON DC   
48      6014               JOLIMONT    WA       OSBORNE PARK DC   
49      6004             EAST PERTH    WA  CITY DELIVERY CENTRE   
50      6104                  ASCOT    WA          WELSHPOOL DC   
51      6057           HIGH WYCOMBE    WA          WALLISTON DC   
52      6014                FLOREAT    WA       OSBORNE PARK DC   
53      6050           MOUNT LAWLEY    WA         BASSENDEAN DC   
54      6051               MAYLANDS    WA         BASSENDEAN DC   
55      6016         MOUNT HAWTHORN    WA       OSBORNE PARK DC   
56      6050              COOLBINIA    WA         BASSENDEAN DC   
57      6017           OSBORNE PARK    WA       OSBORNE PARK DC   
58      6062               EMBLETON    WA         B

In [26]:
from sklearn.linear_model import LinearRegression

In [27]:
lm = LinearRegression()
lm

LinearRegression()

In [66]:
Z = df_Perth_House[['DistanceFromCBD_KM', 'DistanceFromCoast', 'North_South']]

In [67]:
lm.fit(Z, df_Perth_House['Median_House_Price'])

LinearRegression()

In [68]:
lm.intercept_

1076920.2351230418

In [69]:
lm.coef_

array([-12151.63633179,  -9280.56024013, -57908.39409962])

In [70]:
print('The R-square is: ', lm.score(Z, df_Perth_House['Median_House_Price']))

The R-square is:  0.24365924256206362


In [54]:
lm1 = LinearRegression()
lm1

LinearRegression()

In [71]:
lm1.fit(df_Perth_House[['North_South']], df_Perth_House['Median_House_Price'])
lm1

LinearRegression()

In [72]:
X = df_Perth_House[['North_South']]
Y =  df_Perth_House['Median_House_Price']

In [73]:
print('The R-square is: ', lm1.score(X, Y))

The R-square is:  0.04946458600619841


## Conclusions Housing Data

### Housing Price data from [RealEstate.com.au](https://www.realestate.com.au/neighbourhoods/) on the 2 JULY 2021

#### Linear regression gave very low R^2 values when plotting house prices based on approximate distance from the coast, North and South of the Swan River and distance from the Perth CBD. For instance, in the Midland Delivery area, Midland has the lowest mean house price of all the suburbs in Perth, but it is surronded by far more affluent suburbs. The most affluent suburb is Cottesloe with a median house price of over 2 million dollars which is on the coast and near the CBD. Traditionally, in Perth they talk about "North and South of the River" North of the River Swan having the more affluent suburbs, this certainly does not seem to be the case oin 2021 since "Affluent Suburbs" seem to be equally distributed al over the Greater Perth Metropolitan Area. There are only three suburbs in the whole of Perth (in my n = 80 sampled data set) with an average house price of less than 300000 dollars, Midland, Greenfields in Mandurah and COOLOONGUP in Rockingham. I have driven through Greenfields along Lakes Road many times and it does not look poor all the house are in good condition. Mandurah, which is a popular city for fly in fly out mining workers (FIFO) has most of the cheaper suburbs being the furtherst form the CBD it is also on the coast. Mandurah has some very attractive looking suburbs and the most expensive are Wannanup and San Remo with a median house prices of 540000 and 575000 dollars, respectively.
[WANNANUP](https://www.realestate.com.au/neighbourhoods/wannanup-6210-wa)
[SAN REMO](https://www.realestate.com.au/neighbourhoods/san-remo-6210-wa)